In [ ]:
# NECESSARY CELL TO REMOVE THE DOWNLOAD AND EXECUTE BUTTONS FROM THE PAGE 

# From Weights to Functions

For this part of the course we keep working with the familiar basis function models we have been using:

$$
y(\bx) = \bw^\T\basis(\bx)
$$(kernelyfunc)

where for regression problems we would use it directly together with some observation noise to define our targets, while in classification we would first feed it into a logistic sigmoid before using it. 

For now let us leave the application aside and just assume we have a vector with values of $y(\bx)$ for several $\bx$. Using the expression above and defining $\Basis_{nk}=\basis_k(\bx_n)$ we have:

$$
\mbf{y} = \Basis\bw
$$(kernelyvec)
 
and since $p(\bw)=\mathcal{N}(\mbf{0},\alpha^{-1}\mbf{I})$ and we can therefore grab as many samples of $\bw$ from our bag as we want, that means $\mbf{y}$ is also **jointly Gaussian**:

$$
p(\mbf{y}) = \gauss\left(\mbf{y}\vert\mbf{0},\displaystyle\frac{1}{\alpha}\Basis\Basis^\T\right)
\equiv
\gauss\left(\mbf{y}\vert\mbf{0},\mbf{K}\right)
$$(kerneljointgaussy)

where you can see that $\bw$ vanished, and we can instead just sample from $\mbf{y}$ instead of $\bw$!

```{admonition} Further Reading    
:class: tip    
If you are interested in the exact derivation of going from $\bw$ to $\mbf{y}$, read Section 6.1 and the beginning of 6.4.1.
+++                         
{bdg-danger}`bishop-prml`     
``` 

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from myst_nb import glue
from matplotlib.lines import Line2D
from cycler import cycler
import seaborn as sns

# Set the color scheme
sns.set_theme()
colors = ['#0076C2', '#EC6842', '#A50034', '#009B77', '#FFB81C', '#E03C31', '#6CC24A', '#EF60A3', '#0C2340', '#00B8C8', '#6F1D77']
plt.rcParams['axes.prop_cycle'] = cycler(color=colors)

M = 9
s = 2.*np.pi/float(M)
alpha = 5.0
beta = 100.0

def bayes(m_prior,L_prior,xval,x=None,y=None):
    centers = np.linspace(0.,2.*np.pi,M)

    if x:
        n = len(x)

        gram = np.zeros((n,M+1))
        gram[:,0] = 1.0

        for i in range(n):
            for j in range(M):
                gram[i,j+1] = np.exp(-(x[i]-centers[j])**2.0/2.0/s/s)

        L_post =  L_prior + beta * gram.transpose() @ gram

        S_post = np.linalg.inv(L_post)

        m_post = S_post @ (L_prior @ m_prior + beta * gram.transpose() @ y)
    else:
        m_post = m_prior
        L_post = L_prior
        S_post = np.linalg.inv(L_prior)
                  
    yval = np.zeros(len(xval))
    yvar = np.zeros(len(xval))
    
    for i in range(len(xval)):
        features = np.zeros(M+1)
        features[0] = 1.0
        for j in range(M):
            features[j+1] = np.exp(-(xval[i]-centers[j])**2.0/2.0/s/s)
        yval[i] = np.inner(features,m_post)
        yvar[i] = 1./beta + np.inner(features,np.matmul(S_post,features))

    return m_post, L_post, yval, yvar

def sample(m,L,xval):
    centers = np.linspace(0.,2.*np.pi,M)
    
    S = np.linalg.inv(L)
    
    w = np.random.multivariate_normal(m,S)
   
    yval = np.zeros(len(xval))
    yvar = np.zeros(len(xval))

    for i in range(len(xval)):
        features = np.zeros(M+1)
        features[0] = 1.0
        for j in range(M):
            features[j+1] = np.exp(-(xval[i]-centers[j])**2.0/2.0/s/s)
        yval[i] = np.inner(features,w)

    return yval

N = 5
n_samples = 10

np.random.seed(101230)

xval = np.linspace(0,2.*np.pi,1000)

prior_mean = np.zeros(M+1)
prior_prec = alpha*np.eye(M+1)

_,_,y_map, y_var = bayes(prior_mean,prior_prec,xval)

fig, ax1 = plt.subplots(1,1,figsize=(5,3),dpi=400)
ax1.set_xlabel('x')
ax1.set_ylabel('y')

handles, labels = ax1.get_legend_handles_labels()
line = Line2D([0], [0], color='gray', lw=1)
handles.append(line)
labels.append('y(x) samples')
ax1.legend(handles=handles, labels=labels, fontsize=7)

for i in range(n_samples):
    y_sample = sample(prior_mean,prior_prec,xval)
    ax1.plot(xval,y_sample,linewidth=1)

glue("fig0", fig, display=False)

We have actually already seen an example of this before when looking at {doc}`../../2-bayesregression/lectures/active_learning`. For a set of radial basis functions and sampling from the prior over $\bw$ we got the following samples:

```{glue:figure} fig0
:figwidth: 500px

Samples from a basis function model obtained by sampling from the prior $p(\bw)$ and plotting the resulting $y(x)$. The same curves could also have been directly sampled from $p(\mbf{y})$ instead.
```

If we instead sampled from Eq. {eq}`kerneljointgaussy` we would get very similar curves. But how does one **sample a function**? That might feel a bit weird, but it is actually straightforward: each curve above is composed of 1000 $y$ values for different $x$. To get one of them we just need to compute the $1000\times 1000$ matrix $\mbf{K}$ and sample from the size-1000 version of Eq. {eq}`kerneljointgaussy`.

Each entry in $\mbf{K}$ relates two different values of $\bx$. We can write one of these entries as:

$$
K_{mn} = k(\bx_m,\bx_n) = \displaystyle\frac{1}{\alpha}\basis(\bx_m)^\T\basis(\bx_n)
$$(kernelbasisfunctionkernel)

and we call $k(\bx_m,\bx_n)$ a **kernel function**.